In [1]:
##load data from .mat file
#get path
import os
import pandas as pd
import numpy as np
import copy
dirname= os.path.abspath(os.getcwd())

In [2]:
df_labels = pd.read_csv(os.path.join(dirname,'biovid_features/sens_temp.csv'))
df_labels
import scipy.stats as stats
input_th_z = stats.zscore(df_labels.pain_threshold)
input_to_z = stats.zscore(df_labels.pain_tolerance)
input_th_to_z = (input_th_z+input_to_z)/2
print(input_th_to_z.shape)

(87,)


In [3]:
#leave subject out cv, LSOCV
def LSOCV(input_subj,input_data,input_label,test_subj):
    test_index=input_subj.index(test_subj)
    test_data=input_data[test_index]
    test_label=input_label[test_index]
    
    train_data=copy.deepcopy(input_data)
    train_data.pop(test_index)
    train_data=np.vstack(train_data)

    train_label=copy.deepcopy(input_label)
    train_label.pop(test_index)
    train_label=np.hstack(train_label)
    
    return train_data,train_label,test_data,test_label

#leave subject out cv with random subject hold-out for tuning
def LSOCV_TUNE(input_subj,input_data,input_label,test_subj):
    #print(test_subj)
    test_index=input_subj.index(test_subj)
    #print(test_index)
    test_data=input_data[test_index]
    test_label=input_label[test_index]   
    
    tune_data=[]
    tune_label=[]
    
    train_data=[]
    train_label=[]
    
    full_subj = input_subj
    full_subj = np.delete(full_subj,test_subj-1)
    #print(full_subj)
    
    hold_out_subj = np.random.choice(full_subj,size = 18, replace = False)
    #print(hold_out_subj)
    #print(hold_out)
    for subj in hold_out_subj:   
        index_hold = input_subj.index(subj)
        #print(index_keep)
        tune_data.append(input_data[index_hold])
        tune_label.append(input_label[index_hold])
        
    train_subj = [i for i in full_subj if i not in hold_out_subj]
    #print(train_subj)
    for subj in train_subj:   
        index_train = input_subj.index(subj)
        #print(index_keep)
        train_data.append(input_data[index_train])
        train_label.append(input_label[index_train])
        
    train_data = np.vstack(train_data)
    train_label = np.hstack(train_label)
    
    tune_data = np.vstack(tune_data)
    tune_label = np.hstack(tune_label)
    
    return train_data,train_label,tune_data,tune_label,test_data,test_label

In [4]:
import torch
import torch.nn as nn
#from pytorch_model_summary import summary

# input_size: the number of expected features in the input x
# batch_first – If True, then the input and output tensors are provided as (batch, seq, feature). 
class PainNet(nn.Module):
    def __init__(self, output_size, input_size, hidden_dim,channel_num):
        super(PainNet, self).__init__()
        self.input_size = input_size
        self.output_size = output_size
        
        self.fc1 = nn.Sequential(nn.Linear(input_size-1, 32),
                               nn.Sigmoid(),
                               nn.Linear(32, 16),
                               nn.Sigmoid(),
                               nn.Linear(16, 6),
                               nn.Sigmoid())
        #for attention
        self.bn = nn.BatchNorm2d(channel_num)
        #nn.init.kaiming_normal_(self.bn.weight)
        nn.init.normal_(self.bn.weight.data, mean=1, std=0.02)
        self.avg_pool = nn.AdaptiveAvgPool2d(1)
        self.max_pool = nn.AdaptiveMaxPool2d(1)
           
        self.fc2 = nn.Sequential(nn.Conv2d(channel_num, 1, 1, bias=False),
                               nn.ReLU(),
                               nn.Conv2d(1, channel_num, 1, bias=False))
        self.ChannelAttention = nn.Sigmoid()
        for p in self.fc2.parameters():
            nn.init.kaiming_normal_(p)
            
        self.bn1D_input = nn.BatchNorm1d(input_size-1)
        self.bn1D_output = nn.BatchNorm1d(6+1)
        self.output = nn.Sequential(nn.Linear(6+1,output_size),
                                    nn.Softmax(dim = 1))

    
    def forward(self, x):
        batch_size = x. size(0)
        #print(x.shape)
        attention = x[:,1:x.size(1),1:x.size(2)].float()#D2: 0,1,2补位，3~attention
        #print(attention.shape)
        x_data = x[:,0,1:x.size(2)].float()#D2: 0,1,2 sensitivity, 3~ 数据
        personalize = x[:,0,0:1].float()
        
        #修改attention维度
        attention = torch.swapaxes(attention,2,1)
        #print(attention.shape)
        attention = torch.unsqueeze(attention, axis = 3)
        #print(attention.shape)
        
        x_ca = self.bn(attention)
        avg_out = self.fc2(self.avg_pool(x_ca))
        #max_out = self.fc2(self.max_pool(x_ca))
        #temp = avg_out + max_out
        temp = avg_out
        ca = self.ChannelAttention(temp)
        ca = ca.squeeze()
        #print(ca.shape)
        x_data = self.bn1D_input(x_data)
        x_data = ca*x_data
        #print(x_data.shape)
        #print(personalize.shape)
        out = self.fc1(x_data)
        personalize_x = torch.cat((out,personalize),1)
        personalize_x = self.bn1D_output(personalize_x)
        out = self.output(personalize_x)
        
        return out     
    
activation = {}
def get_activation(name):
    def hook(model, input, output):
        activation[name] = output.detach()
    return hook

In [5]:
def Perf_evaluation(data_loader, batch_size):
    num_correct = 0
    count=0
    
    for inputs, labels in data_loader:
        count=count+1
        inputs, labels = inputs.to(device), labels.to(device)
        output = model(inputs)
        output = torch.argmax(output,dim = 1)
        
        pred = output.squeeze()
        pred=pred.cpu().detach().numpy()
        pred=np.reshape(pred,(-1))
        pred_01 = pred
        
        labels=np.reshape(labels.cpu(),(-1))
        if count==1:
            all_pred=pred
            all_pred_01 = pred_01
            all_label=labels

        else:
            all_pred=np.hstack((all_pred,pred))
            all_label=np.hstack((all_label,labels))
            all_pred_01=np.hstack((all_pred_01,pred_01))

    acc = num_correct/(count*batch_size)

    #print("Accuracy: {:.3f}%".format(acc*100))
    #print("Confusion matrix:")
    #print(confusion_matrix(all_label, all_pred))
    
    return all_pred, all_pred_01, all_label

In [6]:
from torch.utils.data import TensorDataset, DataLoader
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix, f1_score, roc_auc_score,accuracy_score
from sklearn.metrics import confusion_matrix

#seq_lens = (2,4,6,8,10,12,15)
seq_lens = (2,4,6,8,10,15,20,25,30,35,40,45,50,55,60)
for seq_len in seq_lens:
    df = pd.read_csv(os.path.join(dirname,'biovid_features/updated_fusion_five_classes'+str(seq_len)+'.csv'))
    df_att = pd.read_csv(os.path.join(dirname,'biovid_features/updated_fusion_five_classes_attention'+str(seq_len)+'.csv'))
    index_remove = df.loc[df['sdnn'] == 0].index
    index_remove = index_remove.unique()
    for i in range(seq_len):
        df_att = df_att.drop(index_remove*seq_len+i)

    df_att.reset_index(inplace = True)
    del df_att["index"]

    del df_att["hf"]
    del df_att["lf"]
    del df_att["lf_hf"]
    del df_att["sampen"]
    del df_att["resp_mean"]
    
    df = df.loc[~(df['sdnn'] == 0)]
    #df["label"].replace({2:1},inplace=True)
    df.reset_index(inplace = True)
    del df["index"]

    del df["hf"]
    del df["lf"]
    del df["lf_hf"]
    del df["sampen"]
    del df["resp_mean"]
    
    
    step = seq_len

    input_data = []
    input_label = []
    input_subj = []

    #for each subject
    person_count = 0
    for subj in np.unique(df.subj_id.values):
        idx = df.index[df['subj_id']==subj]
        data2D = df.iloc[idx,2:].values
        label2D = df.iloc[idx,1].values
    
        print(data2D.shape)
        print(np.count_nonzero(label2D==1) )
    
        person_sens_threshold = np.full((data2D.shape[0],1),input_th_to_z[person_count])
        person_count = person_count+1
        #update data2D with personal sensitivity
        data2D = np.concatenate((person_sens_threshold,data2D),axis = 1) 
        print(data2D.shape)

        input_data.append(data2D)
        input_label.append(label2D)
        input_subj.append(subj)
     
    at_input_data = []
    at_input_label = []
    at_input_subj = []

    #for each subject
    for subj in np.unique(df_att.subj_id.values):
        idx = df_att.index[df_att['subj_id']==subj]
        data2D_ = df_att.iloc[idx,2:].values
        label2D_ = df_att.iloc[idx,1].values
        print(data2D_.shape)
    
        #补位，为了与input_data维度保持一致
        patch_data = np.zeros((data2D_.shape[0],1))
    
        #update data2D with personalHRV
        data2D_ = np.concatenate((patch_data,data2D_),axis = 1) #column0:3 personal HRV, column3:end features
    
        #data_len = len(data2D_) - seq_len + 1
        data_len = int(len(data2D_)/seq_len)   #initial an empty array 其他的notebook，改这里
        print(data_len)
        data3D=np.empty((data_len,seq_len,data2D_.shape[1]))#empty
        label3D=np.empty((data_len,))#many to one label
    
        for i in range(data_len):
            data3D[i,:,:]=data2D_[i*step : i*step+seq_len,:]
            label3D[i]=label2D_[i*step+seq_len-1] #-1
    
        print(data3D.shape)
        #print(np.count_nonzero(label3D))
    
        at_input_data.append(data3D)
        at_input_label.append(label3D)
        at_input_subj.append(subj)

        
    for i in np.unique(input_subj):
        if(torch.cuda.is_available()):
            device="cuda:1"
        #device="cpu"
        else:
            device="cpu"
    
        print(device)

        input_size = data2D.shape[1]
        output_size = 5
        hidden_dim  = 128
        criterion = nn.CrossEntropyLoss()
        def adjust_learning_rate(epoch):
            lr = 0.01*(0.1**(epoch//50))
            return lr
        epochs = 50
        print_every = 10
        clip = 5
    
    
        if i>-1: #以防需要筛选:
            model = PainNet(output_size, input_size, hidden_dim,channel_num = input_size-1)
            model.to(device)
        
            model.ChannelAttention.register_forward_hook(get_activation('ChannelAttention'))
        
            counter = 0
            acc_min = 0
            test_subj = i
            print(len(input_subj))
            print(len(input_data))
            print(len(input_label))

            print("test_subject: {}".format(test_subj))
        
      #  #leave-subject-out cross-validation, in training phase 80% of training dataset train, 20% person tuning
      #  [train_data,train_label,tune_data, tune_label,test_data,test_label]=LSOCV_TUNE(input_subj,input_data,
      #                                                                                 input_label,test_subj=test_subj)
      #  print(train_data.shape, train_label.shape, tune_data.shape, tune_label.shape,
      #       test_data.shape, test_label.shape)
        
            #leave-subject-out cross-validation, in training phase 80% of training dataset train, 20% data tuning
            [train_data,train_label,test_data,test_label]=LSOCV(input_subj,input_data,input_label,test_subj=test_subj)
            [train_data,tune_data, train_label, tune_label]= train_test_split(train_data,train_label, test_size = 0.2, random_state = 42)
        
            print(train_data.shape, train_label.shape, tune_data.shape, tune_label.shape,
                 test_data.shape, test_label.shape)
            [train_attention,train_att_label,test_attention,test_att_label]=LSOCV(input_subj,at_input_data,at_input_label,test_subj=test_subj)
            [train_attention,tune_attention, train_att_label, tune_att_label]= train_test_split(
                train_attention,train_att_label, test_size = 0.2, random_state = 42)
        
            train_data = np.reshape(train_data,(train_data.shape[0],1,train_data.shape[1]))
            train_data = np.concatenate((train_data,train_attention),axis = 1)
            tune_data = np.reshape(tune_data,(tune_data.shape[0],1,tune_data.shape[1]))
            tune_data = np.concatenate((tune_data,tune_attention),axis = 1)
            test_data = np.reshape(test_data,(test_data.shape[0],1,test_data.shape[1]))
            test_data = np.concatenate((test_data,test_attention),axis = 1)
        
            train_label = torch.from_numpy(train_label)
            tune_label = torch.from_numpy(tune_label)
            test_label = torch.from_numpy(test_label)
                
        #对不同类的样本赋予权重，然后进行权重采样
        #count num of different classes

            print('target train 0/1: {}/{}'.format(
                (train_label == 0).sum(), (train_label != 1).sum()))
      
            train_label = train_label
       
            test_label = test_label
        
            batch_size = test_label.shape[0]
            print(train_data.shape,train_label.shape,tune_data.shape,tune_label.shape,test_data.shape,test_label.shape)
            print(type(train_data),type(train_label), type(test_data), type(test_label))

            dataset_training = TensorDataset(torch.from_numpy(train_data),train_label)
            dataset_tuning = TensorDataset(torch.from_numpy(tune_data),tune_label)
            dataset_test = TensorDataset(torch.from_numpy(test_data),test_label)

            train_loader = DataLoader(dataset_training, shuffle=False, batch_size=batch_size, drop_last=False)
            tuning_loader = DataLoader(dataset_tuning, shuffle=False, batch_size=batch_size, drop_last=False)
            test_loader = DataLoader(dataset_test, shuffle=False, batch_size=batch_size, drop_last=False)
    
            model.train()
    
            for e in range(epochs):
                learning_rate = adjust_learning_rate(e)
                optimizer = torch.optim.Adam(model.parameters(), lr = learning_rate)
    
                for inputs, labels in train_loader:
                    model.train()
                    counter += 1
        
                    inputs, labels = inputs.to(device), labels.to(device)
            
                    model.zero_grad()
                    output = model(inputs)
                    #output = torch.argmax(output,dim = 1)
                
                    loss = criterion(output, labels)
                    loss.backward()

                    nn.utils.clip_grad_norm_(model.parameters(), clip)
                    optimizer.step()
       
                    if counter%print_every == 0:
                        #evaluate on validation data
                        model.eval()
                        [tuning_pred, tuning_pred_01, tuning_label] = Perf_evaluation(tuning_loader, batch_size)
                        acc = accuracy_score(tuning_label, tuning_pred);
                        if acc>acc_min:
                            [test_pred, test_pred_01, test_label] = Perf_evaluation(test_loader, batch_size)
                            acc_test = accuracy_score(test_label, test_pred);
                            print("Epoch: {}/{}...".format(e+1, epochs),
                                "Step: {}...".format(counter),
                              "Loss: {:.6f}...".format(loss.item()))
                            #torch.save(model.state_dict(), './test.pt')
                            print("Tuning acc improved({:.3f}-->{:.3f}). Saving model...".format(acc_min, acc))
                            print("Test acc {:.3f}".format(acc_test))
                            print("Confusion matrix:")
                            print(confusion_matrix(test_label, test_pred_01))
                            acc_min = acc
                            test_result = pd.DataFrame({"pred":test_pred,"label":test_label, "pred_01":test_pred_01})
                            test_save_path = 'biovid_revision_results/lengths_biovid_5classes_sensmeasure/'+str(seq_len)+'_test'+str(test_subj)+'.xlsx'
                            test_result.to_excel(os.path.join(dirname,test_save_path))

(98, 15)
19
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
19
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
19
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
19
(98, 16)
(98, 15)
19
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
19
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
19
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
19
(98, 16)
(98, 15)
19
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
19
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
19
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
19
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
20
(98, 16)
(98, 15)
19
(98, 16)
(98, 15)
19
(98, 16)
(98, 15)
19
(

Epoch: 48/50... Step: 3280... Loss: 1.420102...
Tuning acc improved(0.384-->0.386). Saving model...
Test acc 0.510
Confusion matrix:
[[17  2  0  0  0]
 [ 2  5 11  1  0]
 [ 2  2 13  3  0]
 [ 1  2  7  2  8]
 [ 3  0  1  3 13]]
cuda:1
87
87
87
test_subject: 2
(6742, 16) (6742,) (1686, 16) (1686,) (98, 16) (98,)
target train 0/1: 1350/5402
(6742, 3, 16) torch.Size([6742]) (1686, 3, 16) torch.Size([1686]) (98, 3, 16) torch.Size([98])
<class 'numpy.ndarray'> <class 'torch.Tensor'> <class 'numpy.ndarray'> <class 'torch.Tensor'>
Epoch: 1/50... Step: 10... Loss: 1.576102...
Tuning acc improved(0.000-->0.167). Saving model...
Test acc 0.194
Confusion matrix:
[[19  0  0  0  0]
 [20  0  0  0  0]
 [19  0  0  0  0]
 [20  0  0  0  0]
 [20  0  0  0  0]]
Epoch: 1/50... Step: 20... Loss: 1.521021...
Tuning acc improved(0.167-->0.184). Saving model...
Test acc 0.255
Confusion matrix:
[[19  0  0  0  0]
 [20  0  0  0  0]
 [18  0  0  0  1]
 [18  0  0  0  2]
 [14  0  0  0  6]]
Epoch: 1/50... Step: 30... Loss:

Epoch: 27/50... Step: 1810... Loss: 1.486112...
Tuning acc improved(0.383-->0.386). Saving model...
Test acc 0.429
Confusion matrix:
[[19  0  0  0  0]
 [ 4  5  2  3  6]
 [ 0  0  0  5 15]
 [ 0  0  1  0 19]
 [ 1  0  0  0 18]]
Epoch: 33/50... Step: 2230... Loss: 1.451529...
Tuning acc improved(0.386-->0.387). Saving model...
Test acc 0.449
Confusion matrix:
[[19  0  0  0  0]
 [ 2  5  2  6  5]
 [ 0  0  0  8 12]
 [ 0  0  0  2 18]
 [ 1  0  0  0 18]]
cuda:1
87
87
87
test_subject: 4
(6742, 16) (6742,) (1686, 16) (1686,) (98, 16) (98,)
target train 0/1: 1350/5405
(6742, 3, 16) torch.Size([6742]) (1686, 3, 16) torch.Size([1686]) (98, 3, 16) torch.Size([98])
<class 'numpy.ndarray'> <class 'torch.Tensor'> <class 'numpy.ndarray'> <class 'torch.Tensor'>
Epoch: 1/50... Step: 10... Loss: 1.565657...
Tuning acc improved(0.000-->0.211). Saving model...
Test acc 0.204
Confusion matrix:
[[ 0 19  0  0  0]
 [ 0 20  0  0  0]
 [ 0 19  0  0  0]
 [ 0 20  0  0  0]
 [ 0 20  0  0  0]]
Epoch: 1/50... Step: 30... Lo

Epoch: 30/50... Step: 2040... Loss: 1.450373...
Tuning acc improved(0.391-->0.395). Saving model...
Test acc 0.286
Confusion matrix:
[[ 9  5  1  0  4]
 [ 9  7  3  1  0]
 [11  5  1  1  2]
 [ 8  3  2  1  5]
 [ 3  6  1  0 10]]
cuda:1
87
87
87
test_subject: 6
(6742, 16) (6742,) (1686, 16) (1686,) (98, 16) (98,)
target train 0/1: 1350/5407
(6742, 3, 16) torch.Size([6742]) (1686, 3, 16) torch.Size([1686]) (98, 3, 16) torch.Size([98])
<class 'numpy.ndarray'> <class 'torch.Tensor'> <class 'numpy.ndarray'> <class 'torch.Tensor'>
Epoch: 1/50... Step: 10... Loss: 1.578780...
Tuning acc improved(0.000-->0.185). Saving model...
Test acc 0.194
Confusion matrix:
[[ 0 19  0  0  0]
 [ 0 19  0  0  0]
 [ 0 20  0  0  0]
 [ 0 20  0  0  0]
 [ 0 18  0  2  0]]
Epoch: 1/50... Step: 20... Loss: 1.552252...
Tuning acc improved(0.185-->0.222). Saving model...
Test acc 0.214
Confusion matrix:
[[ 0  8  0 11  0]
 [ 0  5  0 14  0]
 [ 0  1  0 19  0]
 [ 0  4  0 16  0]
 [ 0  0  0 20  0]]
Epoch: 1/50... Step: 30... Loss:

Epoch: 36/50... Step: 2450... Loss: 1.479997...
Tuning acc improved(0.377-->0.381). Saving model...
Test acc 0.388
Confusion matrix:
[[12  7  0  0  0]
 [ 6  9  4  0  1]
 [ 4 12  4  0  0]
 [ 5  7  6  0  1]
 [ 1  3  2  1 13]]
cuda:1
87
87
87
test_subject: 8
(6742, 16) (6742,) (1686, 16) (1686,) (98, 16) (98,)
target train 0/1: 1350/5409
(6742, 3, 16) torch.Size([6742]) (1686, 3, 16) torch.Size([1686]) (98, 3, 16) torch.Size([98])
<class 'numpy.ndarray'> <class 'torch.Tensor'> <class 'numpy.ndarray'> <class 'torch.Tensor'>
Epoch: 1/50... Step: 10... Loss: 1.546610...
Tuning acc improved(0.000-->0.215). Saving model...
Test acc 0.204
Confusion matrix:
[[ 0  0  0  0 19]
 [ 0  0  0  0 20]
 [ 0  0  0  0 19]
 [ 0  0  0  0 20]
 [ 0  0  0  0 20]]
Epoch: 1/50... Step: 20... Loss: 1.505872...
Tuning acc improved(0.215-->0.224). Saving model...
Test acc 0.204
Confusion matrix:
[[ 0  0  0  0 19]
 [ 0  0  0  0 20]
 [ 0  0  0  0 19]
 [ 0  0  0  0 20]
 [ 0  0  0  0 20]]
Epoch: 1/50... Step: 30... Loss:

...

Epoch: 3/50... Step: 140... Loss: 1.474674...
Tuning acc improved(0.355-->0.356). Saving model...
Test acc 0.340
Confusion matrix:
[[ 0 11  2  3  1]
 [ 1  5  5  7  2]
 [ 0  3  7  6  2]
 [ 0  3  1 11  4]
 [ 1  1  4  5  9]]
Epoch: 3/50... Step: 150... Loss: 1.478931...
Tuning acc improved(0.356-->0.360). Saving model...
Test acc 0.309
Confusion matrix:
[[6 7 2 1 1]
 [7 2 6 3 2]
 [2 1 9 3 3]
 [4 1 3 4 7]
 [4 1 5 2 8]]
Epoch: 4/50... Step: 220... Loss: 1.551957...
Tuning acc improved(0.360-->0.366). Saving model...
Test acc 0.330
Confusion matrix:
[[5 7 2 2 1]
 [5 2 7 3 3]
 [1 1 9 6 1]
 [3 1 3 6 6]
 [3 1 4 3 9]]
Epoch: 5/50... Step: 320... Loss: 1.510660...
Tuning acc improved(0.366-->0.368). Saving model...
Test acc 0.266
Confusion matrix:
[[4 9 0 3 1]
 [5 9 0 3 3]
 [1 8 0 6 3]
 [2 4 0 4 9]
 [5 2 0 5 8]]
Epoch: 12/50... Step: 810... Loss: 1.483890...
Tuning acc improved(0.368-->0.368). Saving model...
Test acc 0.298
Confusion matrix:
[[ 2 10  0  4  1]
 [ 1  8  0  8  3]
 [ 0  7  0 10  1]
 

Epoch: 5/50... Step: 280... Loss: 1.471487...
Tuning acc improved(0.363-->0.369). Saving model...
Test acc 0.404
Confusion matrix:
[[ 0  6  6  3  2]
 [ 0  7  6  3  2]
 [ 0  3 10  5  1]
 [ 0  0  0  1 19]
 [ 0  0  0  0 20]]
Epoch: 10/50... Step: 680... Loss: 1.514812...
Tuning acc improved(0.369-->0.371). Saving model...
Test acc 0.415
Confusion matrix:
[[ 0 14  1  1  1]
 [ 0 14  0  3  1]
 [ 0 16  2  0  1]
 [ 0  0  0  3 17]
 [ 0  0  0  0 20]]
Epoch: 10/50... Step: 690... Loss: 1.494435...
Tuning acc improved(0.371-->0.373). Saving model...
Test acc 0.457
Confusion matrix:
[[ 0  8  7  1  1]
 [ 1  5  9  3  0]
 [ 0  3 15  1  0]
 [ 0  0  0  8 12]
 [ 0  0  0  5 15]]
Epoch: 11/50... Step: 750... Loss: 1.441569...
Tuning acc improved(0.373-->0.379). Saving model...
Test acc 0.426
Confusion matrix:
[[ 0 13  2  0  2]
 [ 0 14  0  3  1]
 [ 0 15  3  0  1]
 [ 0  0  0  3 17]
 [ 0  0  0  0 20]]
Epoch: 14/50... Step: 960... Loss: 1.484333...
Tuning acc improved(0.379-->0.383). Saving model...
Test acc 0

Epoch: 7/50... Step: 460... Loss: 1.468307...
Tuning acc improved(0.365-->0.370). Saving model...
Test acc 0.319
Confusion matrix:
[[ 9  5  0  2  1]
 [ 4 11  0  1  2]
 [ 3 10  0  3  3]
 [ 4  4  1  4  7]
 [ 3  8  0  3  6]]
Epoch: 9/50... Step: 610... Loss: 1.514628...
Tuning acc improved(0.370-->0.376). Saving model...
Test acc 0.287
Confusion matrix:
[[ 9  7  0  0  1]
 [ 3 12  1  0  2]
 [ 3 11  1  3  1]
 [ 1  7  4  2  6]
 [ 0 12  2  3  3]]
Epoch: 10/50... Step: 680... Loss: 1.496671...
Tuning acc improved(0.376-->0.381). Saving model...
Test acc 0.298
Confusion matrix:
[[ 8  7  0  1  1]
 [ 3 12  1  0  2]
 [ 3 10  1  4  1]
 [ 2  6  3  3  6]
 [ 0 12  1  3  4]]
Epoch: 25/50... Step: 1670... Loss: 1.441088...
Tuning acc improved(0.381-->0.390). Saving model...
Test acc 0.351
Confusion matrix:
[[11  5  0  1  0]
 [ 3 12  0  1  2]
 [ 4  9  1  2  3]
 [ 3  5  1  6  5]
 [ 3  9  3  2  3]]
Epoch: 29/50... Step: 1950... Loss: 1.389817...
Tuning acc improved(0.390-->0.390). Saving model...
Test acc 

Epoch: 34/50... Step: 2320... Loss: 1.433793...
Tuning acc improved(0.385-->0.386). Saving model...
Test acc 0.372
Confusion matrix:
[[16  0  0  1  0]
 [ 6  7  4  1  0]
 [11  5  3  0  0]
 [ 1  2  9  8  0]
 [ 0  2  7 10  1]]
Epoch: 36/50... Step: 2460... Loss: 1.466128...
Tuning acc improved(0.386-->0.392). Saving model...
Test acc 0.330
Confusion matrix:
[[15  0  2  0  0]
 [ 6  6  6  0  0]
 [ 9  6  3  0  1]
 [ 1  1 12  6  0]
 [ 0  1 12  6  1]]
cuda:1
87
87
87
test_subject: 52
(6461, 16) (6461,) (1616, 16) (1616,) (95, 16) (95,)
target train 0/1: 1176/5153
(6461, 46, 16) torch.Size([6461]) (1616, 46, 16) torch.Size([1616]) (95, 46, 16) torch.Size([95])
<class 'numpy.ndarray'> <class 'torch.Tensor'> <class 'numpy.ndarray'> <class 'torch.Tensor'>
Epoch: 1/50... Step: 10... Loss: 1.579205...
Tuning acc improved(0.000-->0.197). Saving model...
Test acc 0.211
Confusion matrix:
[[ 0  0  0 17  0]
 [ 0  0  0 19  0]
 [ 0  0  0 19  0]
 [ 0  0  0 20  0]
 [ 0  0  0 20  0]]
Epoch: 1/50... Step: 20..

ValueError: Expected more than 1 value per channel when training, got input size torch.Size([1, 15])